In [1]:
import pandas as pd
import numpy as np
import nltk
import sklearn
import string
import re
from collections import defaultdict
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.pyplot as plt
import seaborn as sns
import pickle
from lxml import html
import nltk
from nltk.stem.snowball import EnglishStemmer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from sklearn.manifold import TSNE
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import RandomizedSearchCV
from sklearn.multiclass import OneVsRestClassifier
from sklearn.linear_model import SGDClassifier
from sklearn.linear_model import LogisticRegression
from sklearn import metrics
from sklearn.metrics import f1_score,precision_score,recall_score,jaccard_score
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.svm import SVC
from sklearn.model_selection import GridSearchCV
import gensim
from gensim.models import Word2Vec

In [2]:
np.random.seed(42)

In [3]:
data_cleaned = pd.read_csv('data_cleaned.csv',
                           converters={"preprocessedTags": lambda x: x.strip("[]").replace("'","").split(", ")})
data_cleaned = data_cleaned.dropna(subset=['desc'])
data_cleaned.head()

Id                                               desc  \
0  48320518  connect two differ databas one applic asp net ...   
1  48320543  bootstrap 4 navbar disappear resiz screen boot...   
2  48320558  xml transform xslt namespac xml transform xslt...   
3  48320572  convert timestamp date various format swift co...   
4     44247  best practic requir time develop best practic ...   

               preprocessedTags                Tag1     Tag2         Tag3  \
0     [mysql, .net, sql-server]               mysql     .net   sql-server   
1  [html, angular, bootstrap-4]                html  angular  bootstrap-4   
2                         [xml]                 xml      NaN          NaN   
3   [ios, json, date, datetime]                 ios     json         date   
4          [project-management]  project-management      NaN          NaN   

       Tag4 Tag5  
0       NaN  NaN  
1       NaN  NaN  
2       NaN  NaN  
3  datetime  NaN  
4       NaN  NaN

In [4]:
sample = data_cleaned.sample(frac =.99)
sample.shape[0]

32513

# Train/Test split

In [5]:
X = sample['desc']
#Y = sample[['Tag1', 'Tag2', 'Tag3']].astype(str).values.tolist()
Y = sample['preprocessedTags']
mb = MultiLabelBinarizer()
Y_encoded = mb.fit_transform(Y)
X_train, X_test, y_train, y_test = train_test_split(X, Y_encoded, test_size=0.2, random_state=42)

In [6]:
print("Number of data points in training data :", X_train.shape[0])
print("Number of data points in test data :", X_test.shape[0])

Number of data points in training data : 26010
Number of data points in test data : 6503


# TF-IDF

In [7]:
vectorizer = TfidfVectorizer(min_df=0.00009, max_features=5000)
X_train_multilabel = vectorizer.fit_transform(X_train)
X_test_multilabel = vectorizer.transform(X_test)

In [8]:
X_train_multilabel.shape

(26010, 3969)

# Word2Vec

https://www.analyticsvidhya.com/blog/2017/06/word-embeddings-count-word2veec/

In [115]:
w2v = Word2Vec(list(X_train.str.split(' ')), size=3000, window=5, min_count=20, workers=11, iter=100)

In [116]:
def document_vector(doc):
    """Create document vectors by averaging word vectors. Remove out-of-vocabulary words."""
    doc = [word for word in doc if word in w2v.wv.vocab]
    return np.mean(w2v[doc], axis=0)

In [117]:
w2v_train = pd.DataFrame(X_train)
w2v_test = pd.DataFrame(X_test)

In [118]:
w2v_train['doc_vector'] = X_train.apply(document_vector)
w2v_test['doc_vector'] = X_test.apply(document_vector)

<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc59112

<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc59112

<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc59112

<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc59112

<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc59112

...

<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc59112

<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc59112

<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc59112

<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc59112

<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc591122>:4: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  return np.mean(w2v[doc], axis=0)
<ipython-input-116-044bfc59112

In [119]:
w2v_train = list(w2v_train['doc_vector'])
w2v_test = list(w2v_test['doc_vector'])

In [120]:
from sklearn import preprocessing
std_scale = preprocessing.StandardScaler().fit(w2v_train)
w2v_train = std_scale.transform(w2v_train)
w2v_test = std_scale.transform(w2v_test)

In [106]:
w2v_train[0]

array([-2.28615047e-01,  8.36385418e-01,  1.06854407e+00,  6.01852028e-01,
       -1.13217989e-02, -8.24776470e-01,  4.13995337e-02,  6.50834971e-02,
       -9.38855977e-01, -3.87318769e-01, -7.15905439e-01, -1.41537032e+00,
       -5.30541159e-01,  1.29438294e+00, -3.39702252e-01,  2.38373524e-01,
        1.20597399e+00, -6.42682086e-01, -9.02454225e-01,  3.08301183e-01,
       -1.23375126e-01,  2.85574377e-02, -2.03503794e-01,  2.74372989e-01,
       -1.75910487e+00,  3.51005724e-01, -1.23939946e+00,  7.69742151e-01,
       -1.45172915e+00, -3.46582291e-01, -1.15012035e+00, -8.10034547e-02,
        9.81042839e-01, -1.18327136e+00,  2.01812471e-01, -7.53639653e-01,
       -1.44271919e+00,  4.66588025e-01,  1.53728868e+00,  2.96327733e-02,
       -6.03209350e-01,  4.38009241e-01,  6.78546252e-01, -1.33239172e+00,
       -1.18269139e+00,  3.19747713e-01, -1.28038475e-01,  4.35837897e-01,
       -6.62041338e-01, -1.77931245e-01, -4.23664773e-01,  1.37846065e+00,
       -4.46367345e-01,  

# Function to log the results

In [57]:
def log_result(model, preprocess, data, pred, saving=True, scores=None):
    if scores is not None:
        df = scores        
    else:
        df = pd.DataFrame(columns=['Model', 'Preprocess', 'F1_micro', 'Jaccard_Micro'])
        
    f1_micro = metrics.f1_score(data, pred, average = 'micro')
    jaccard_micro = metrics.jaccard_score(data, pred, average = 'micro')
    
    results = {"Model":model, "Preprocess":preprocess,
               "F1_micro":f1_micro, "Jaccard_Micro":jaccard_micro}
    
    df = df.append(results, ignore_index=True)
    return df

# Modeling

## With TF-IDF

https://www.quora.com/Whats-the-difference-between-gradient-descent-and-stochastic-gradient-descent

In [14]:
import warnings
warnings.filterwarnings("ignore")

In [15]:
clf = OneVsRestClassifier(SGDClassifier())

parameters = {
    "estimator__loss": ['hinge', 'log'],
    "estimator__alpha": [1e-3, 1e-2, 1e-1, 1e0],
    "estimator__penalty":['l2', 'l1', 'elasticnet'],
}

model_tunning = GridSearchCV(clf, param_grid=parameters,
                             scoring='jaccard_micro', n_jobs=11,
                             verbose=1)

model_tunning.fit(X_train_multilabel, y_train)

print("Best score:", model_tunning.best_score_)
print("Param:", model_tunning.best_params_)

Best score: 0.344640068697628
Param: {'estimator__alpha': 0.0001, 'estimator__loss': 'log', 'estimator__penalty': 'l1'}


In [16]:
clf = OneVsRestClassifier(SGDClassifier(loss=list(model_tunning.best_params_.values())[1], 
                                        alpha=list(model_tunning.best_params_.values())[0], 
                                        penalty=list(model_tunning.best_params_.values())[2], 
                                        n_jobs=11))
clf.fit(X_train_multilabel,
        y_train)
y_pred = clf.predict(X_test_multilabel)

In [59]:
scores = log_result('SGDC', 'tf_idf', y_test, y_pred, saving=True, scores=None)
scores

Model Preprocess  F1_micro  Jaccard_Micro
0   svc     tf_idf  0.571108       0.399686

In [18]:
clf2 = OneVsRestClassifier(LogisticRegression(penalty='l2', n_jobs=-1))
clf2.fit(X_train_multilabel, y_train)
y_pred2 = clf2.predict(X_test_multilabel)

In [60]:
scores = log_result('Log_reg', 'tf_idf', y_test, y_pred2, saving=True, scores=scores)
scores

Model Preprocess  F1_micro  Jaccard_Micro
0      svc     tf_idf  0.571108       0.399686
1  Log_reg     tf_idf  0.486524       0.321462

In [41]:
param_grid = {'estimator__C': [1, 10],  
              'estimator__gamma': [1, 0.1, 0.01], 
              'estimator__kernel': ['rbf']}
grid_svc = OneVsRestClassifier(SVC())

grid_svc = GridSearchCV(grid_svc, param_grid, refit=True, verbose=1, n_jobs=11)

grid_svc.fit(X_train_multilabel, y_train)

# print best parameter after tuning 
print(grid_svc.best_params_) 

Fitting 5 folds for each of 25 candidates, totalling 125 fits


[Parallel(n_jobs=11)]: Using backend LokyBackend with 11 concurrent workers.
[Parallel(n_jobs=11)]: Done  28 tasks      | elapsed: 74.4min
[Parallel(n_jobs=11)]: Done 125 out of 125 | elapsed: 363.8min finished


GridSearchCV(estimator=OneVsRestClassifier(estimator=SVC()), n_jobs=11,
             param_grid={'estimator__C': [0.1, 1, 10, 100, 1000],
                         'estimator__gamma': [1, 0.1, 0.01, 0.001, 0.0001],
                         'estimator__kernel': ['rbf']},
             verbose=1)

In [49]:
svc = OneVsRestClassifier(SVC(C=list(grid_svc.best_params_.values())[0],
                              kernel=list(grid_svc.best_params_.values())[2],
                              gamma=list(grid_svc.best_params_.values())[1]),
                              random_state=42)

svc.fit(X_train_multilabel, y_train)
y_pred_svc = svc.predict(X_test_multilabel)

In [58]:
scores = log_result('svc', 'tf_idf', y_test, y_pred_svc, saving=True, scores=scores)
scores

Model Preprocess  F1_micro  Jaccard_Micro
0   svc     tf_idf  0.609937       0.438784

## With Word2Vec

In [22]:
clf = OneVsRestClassifier(SGDClassifier())

parameters = {
    "estimator__loss": ['log'],
    "estimator__alpha": [1e-4, 1e-3, 1e-2, 1e-1, 1e0, 1e1, 1e2, 1e3],
    "estimator__penalty":['l2', 'l1', 'elasticnet'],
}

model_tunning = GridSearchCV(clf, param_grid=parameters,
                             scoring='jaccard_micro', n_jobs=11)

model_tunning.fit(w2v_train, y_train)

print("Best score:", model_tunning.best_score_)
print("Param:", model_tunning.best_params_)

Best score: 0.035314778540172787
Param: {'estimator__alpha': 1000.0, 'estimator__loss': 'log', 'estimator__penalty': 'l2'}


In [ ]:
clf = OneVsRestClassifier(SGDClassifier(loss='log', alpha=0.001, penalty='l1', n_jobs=11))
clf.fit(w2v_train,
        y_train)
y_pred = clf.predict(w2v_test)

In [ ]:
metrics.f1_score(y_test, y_pred, average = 'micro')

In [ ]:
scores = log_result('SGDC', 'W2V', y_test, y_pred, saving=True, scores=scores)
scores

In [66]:
svc = OneVsRestClassifier(SVC(C=10,
                              kernel='rbf',
                              gamma=0.1,
                              random_state=42))
svc.fit(w2v_train, y_train)
y_pred_svc_w2v = svc.predict(w2v_test)

[LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM][LibSVM]

In [67]:
scores = log_result('SVC', 'W2V', y_test, y_pred_svc_w2v, saving=True, scores=scores)
scores

Model Preprocess  F1_micro  Jaccard_Micro
0      svc     tf_idf  0.571108       0.399686
1  Log_reg     tf_idf  0.486524       0.321462
2      SVC        W2V  0.048446       0.024825

# Saving Model

In [26]:
pickle.dump(vectorizer, open('Flask/tfidf', 'wb'))
pickle.dump(clf, open('Flask/model', 'wb'))
pickle.dump(mb, open('Flask/mb', 'wb'))

In [27]:
classes_convertor = mb.classes_
classes_convertor = pd.DataFrame(classes_convertor)
classes_convertor.to_csv('Flask/classes_convertor.csv')

# Unsupervized approach

In [31]:
from sklearn.decomposition import LatentDirichletAllocation

In [76]:
n_components = 100
n_top_words = 20

In [79]:
lda = LatentDirichletAllocation(n_components=n_components, max_iter=5,
                                learning_method='online',
                                learning_offset=50.,
                                random_state=42,
                                n_jobs=11)
lda.fit(X_train_multilabel)

LatentDirichletAllocation(learning_method='online', learning_offset=50.0,
                          max_iter=5, n_components=100, n_jobs=11,
                          random_state=42)

In [80]:
lda.bound_

9167.98469959558

In [70]:
def print_top_words(model, feature_names, n_top_words):
    for topic_idx, topic in enumerate(model.components_):
        message = "Topic #%d: " % topic_idx
        message += " ".join([feature_names[i]
                             for i in topic.argsort()[:-n_top_words - 1:-1]])
        print(message)
    print()

In [72]:
feature_names = vectorizer.get_feature_names()

In [81]:
#print_top_words(lda, feature_names, n_top_words)

In [ ]:
# -----------------------------------------------------------------

In [83]:
import gensim

In [86]:
import gensim.corpora as corpora

data_text = list(X.str.split(' '))

# Create Dictionary
id2word = corpora.Dictionary(data_text)

# Create Corpus
texts = data_text.copy()

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]# View
print(corpus[:1])

[[(0, 5), (1, 2), (2, 1), (3, 1), (4, 4), (5, 1), (6, 1), (7, 1), (8, 1), (9, 5), (10, 5), (11, 1), (12, 1), (13, 2), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 2), (21, 3), (22, 1), (23, 2), (24, 5), (25, 1)]]


In [88]:
lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                       id2word=id2word,
                                       num_topics=10, 
                                       random_state=100,
                                       chunksize=100,
                                       passes=10,
                                       per_word_topics=True)

In [89]:
print(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(0, '0.022*"function" + 0.018*"data" + 0.017*"id" + 0.016*"get" + 0.015*"return" + 0.014*"log" + 0.014*"var" + 0.014*"view" + 0.013*"user" + 0.012*"json"'), (1, '0.027*"valu" + 0.027*"array" + 0.023*"list" + 0.016*"number" + 0.013*"print" + 0.013*"use" + 0.013*"return" + 0.013*"name" + 0.013*"n" + 0.012*"get"'), (2, '0.060*"file" + 0.015*"error" + 0.014*"use" + 0.014*"line" + 0.013*"run" + 0.012*"command" + 0.011*"python" + 0.010*"script" + 0.010*"tri" + 0.009*"server"'), (3, '0.092*"java" + 0.040*"com" + 0.036*"android" + 0.028*"org" + 0.020*"app" + 0.012*"core" + 0.011*"intern" + 0.009*"jar" + 0.009*"lang" + 0.009*"run"'), (4, '0.034*"date" + 0.030*"tabl" + 0.026*"00" + 0.020*"select" + 0.020*"queri" + 0.018*"01" + 0.016*"id" + 0.016*"sql" + 0.013*"time" + 0.012*"row"'), (5, '0.046*"3" + 0.033*"5" + 0.032*"4" + 0.029*"column" + 0.024*"data" + 0.021*"c" + 0.020*"6" + 0.016*"10" + 0.015*"row" + 0.014*"7"'), (6, '0.044*"int" + 0.039*"class" + 0.038*"public" + 0.028*"new" + 0.024*"void"

In [92]:
from gensim.models import CoherenceModel# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_text, 
                                     dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Coherence Score:  0.6359926691612999


In [93]:
def compute_coherence_values(corpus, dictionary, k, a, b):
    
    lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=10, 
                                           random_state=100,
                                           chunksize=100,
                                           passes=10,
                                           alpha=a,
                                           eta=b,
                                           per_word_topics=True)
    
    coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
    
    return coherence_model_lda.get_coherence()

In [98]:
import tqdm
grid = {}
grid['Validation_Set'] = {}
# Topics range
min_topics = 2
max_topics = 11
step_size = 1
topics_range = range(min_topics, max_topics, step_size)
# Alpha parameter
alpha = list(np.arange(0.01, 1, 0.3))
alpha.append('symmetric')
alpha.append('asymmetric')
# Beta parameter
beta = list(np.arange(0.01, 1, 0.3))
beta.append('symmetric')
# Validation sets
num_of_docs = len(corpus)
corpus_sets = [# gensim.utils.ClippedCorpus(corpus, num_of_docs*0.25), 
               # gensim.utils.ClippedCorpus(corpus, num_of_docs*0.5), 
               gensim.utils.ClippedCorpus(corpus, num_of_docs*0.75), 
               corpus]
corpus_title = ['75% Corpus', '100% Corpus']
model_results = {'Validation_Set': [],
                 'Topics': [],
                 'Alpha': [],
                 'Beta': [],
                 'Coherence': []
                }# Can take a long time to run
if 1 == 1:
    pbar = tqdm.tqdm(total=540)
    
    # iterate through validation corpuses
    for i in range(len(corpus_sets)):
        # iterate through number of topics
        for k in topics_range:
            # iterate through alpha values
            for a in alpha:
                # iterare through beta values
                for b in beta:
                    # get the coherence score for the given parameters
                    cv = compute_coherence_values(corpus=corpus_sets[i], dictionary=id2word, 
                                                  k=k, a=a, b=b)
                    # Save the model results
                    model_results['Validation_Set'].append(corpus_title[i])
                    model_results['Topics'].append(k)
                    model_results['Alpha'].append(a)
                    model_results['Beta'].append(b)
                    model_results['Coherence'].append(cv)
                    
                    pbar.update(1)
    pd.DataFrame(model_results).to_csv('lda_tuning_results.csv', index=False)
    pbar.close()

  0%|          | 0/540 [00:00<?, ?it/s]

ValueError: Stop argument for islice() must be None or an integer: 0 <= x <= sys.maxsize.

In [99]:
len(corpus)

32513